These are screens are those that I follow from: *What Works on Wall Street, Fourth Edition: The Classic Guide to the Best-Performing Investment Strategies of All Time.* 

This is just my interpretation of the books material.

**This material is not intended to be relied upon as a forecast, research or investment advice, and is not a recommendation. Past performance is not always indicative of future returns. I may or may not own stocks listed**

# R System Prep

Data was downloaded the day that I run this notebook. Data should be 1 market day old.

This sheet was run on: 

In [1]:
Sys.time()

[1] "2022-06-06 15:35:22 PDT"

First initialize R environment:

In [2]:
suppressPackageStartupMessages(library(tidyverse))
suppressPackageStartupMessages(library(tidyquant))
suppressPackageStartupMessages(library(rio))
suppressPackageStartupMessages(library(knitr))
suppressPackageStartupMessages(library(kableExtra))
suppressPackageStartupMessages(library(IRdisplay))
#library(kableExtra)

<!-- TEASER_END -->
Read Data

In [3]:
#setwd("D:/OneDrive/SITES/www.michaelghens.com/Rdocs")
universe <-
  read.csv(
    "STOCKS.TXT",
    header = FALSE,
    stringsAsFactors = FALSE,
    na.strings = '-9999999999.990'
  )

universe_names <-
  read.csv(
    "STOCKS_KEY.TXT",
    header = FALSE,
    stringsAsFactors = FALSE,
    na.strings = '-9999999999.990'
  )

names(universe) <- universe_names[, 2]
count1 <- nrow(universe)[1]

Fields imported:

In [4]:
universe_names[, 2] %>%
  kbl("html") %>%
  as.character() %>%
  display_html()

x 
 
 
 
 
 Ticker 
 
 
 Company name 
 
 
 Price Change 52 week 
 
 
 Yield 
 
 
 Sector 
 
 
 Industry 
 
 
 Exchange 
 
 
 ADR/ADS Stock 
 
 
 Market Cap Q1 
 
 
 Price Change 13 week 
 
 
 Price Change 26 week 
 
 
 Cash flow/share 12m 
 
 
 Shares Average Q1 
 
 
 Sales 12m 
 
 
 Buyback Yield 
 
 
 Price/Book 
 
 
 PE 
 
 
 Price/Sales 
 
 
 Enterprise Value/EBITDA 
 
 
 Price/CFPS 
 
 
 Shareholder Yield 
 
 
 1yr chg debt 
 
 
 External Financing 
 
 
 LT Debt/equity Q1 
 
 
 LT debt/free cash flow 12m 
 
 
 EarningsQuality

Fields:

* EarningsQuality: ([Cash from operations 12m]-[Net income 12m])/[Market Cap Q1]
* 1yr chg debt: [Long-term debt Q1]-[Long-term debt Q5])/[Long-term debt Q5]
* External Financing: [Cash from financing Q1]/[Total assets Q1]

Are caculated fields


To clean up the universe of stocks, they must:

* have a ticker
* market cap
* 13,26,52 week price change
* not be over the counter
* not an ADR stock
* not be a reit stock.
* not be a closed end fund (TBA)

In [5]:
universe <- universe[complete.cases(universe$Ticker),]
universe <- universe[complete.cases(universe$`Market Cap Q1`),]
universe <- universe[complete.cases(universe$`Price Change 13 week`),]
universe <- universe[complete.cases(universe$`Price Change 26 week`),]
universe <- universe[complete.cases(universe$`Price Change 52 week`),]
#exchanges
condition <- c("N - New York", "A - American", "M - Nasdaq")
universe <- filter(universe, Exchange %in% condition)
universe <- filter(universe,`ADR/ADS Stock` == 'FALSE')
universe <- filter(universe,!grepl('REITs',Industry))
count2 <- nrow(universe)[1]

# Market Cap Variables

Screens need some market cap and momentom constants

* Minimum deflated Market Cap all cap universe
* Mediam 13 and 26 Momentom for bear trap
* Average Market cap for large cap universe

Calculating deflator, mins, means and medians.

In [6]:
options("getSymbols.warning4.0"=FALSE)
#find inflation Market Cap 150 @ 1995
getSymbols("CPIAUCSL", src = "FRED", auto.assign=getOption('getSymbols.auto.assign',TRUE))
deflator  <-
  last(Cl(to.yearly(CPIAUCSL)))[[1]] / Cl(to.yearly(CPIAUCSL))['1995'][[1]]
mincap <- 150 * deflator
median13w <- median(universe$`Price Change 13 week`)
median26w <- median(universe$`Price Change 26 week`)
avgmcap <- mean(universe$`Market Cap Q1`,  na.rm = TRUE)
avgshares <- mean(universe$`Shares Average Q1`,  na.rm = TRUE)
avgcashflowshares <- mean(universe$`Cash flow/share 12m`,  na.rm = TRUE)
avgsales15 <- mean(universe$`Sales 12m`,  na.rm = TRUE) * 1.5

[1] "CPIAUCSL"

# Create stock unverses

Screens are based on thre inverses of stocks 

* smallstocks
* allstocks
* largestocks
* marketleaders

## Create means and medians 

In [7]:
smallstocks <- filter(universe, `Market Cap Q1` <= avgmcap & `Market Cap Q1` >= mincap)

allstocks <- filter(universe, `Market Cap Q1` >= mincap)

largestocks <- filter(universe, `Market Cap Q1` >= avgmcap)

marketleaders <- allstocks %>% filter(Sector != "59  - Utilities") %>% 
  filter(`Shares Average Q1` > avgshares) %>%
  filter(`Cash flow/share 12m` > avgcashflowshares) %>%
  filter(`Sales 12m` > avgsales15)

Function to add rankings

In [8]:
calcvc2 <- function(x) {
  #Calculate VC2
  #subtract ntile from 101 to reverse (correct) Order. So Small is big
  x$`Price/Book.Rank` <-
    100 - round(percent_rank(x$`Price/Book`) * 100, 1)
  x$PE.Rank <- 100 - round(percent_rank(x$PE) * 100, 1)
  x$`Price/Sales.Rank` <-
    100 - round(percent_rank(x$`Price/Sales`) * 100, 1)
  x$`Enterprise Value/EBITDA.Rank` <-
    100 - round(percent_rank(x$`Enterprise Value/EBITDA`) * 100, 1)
  x$`Price/CFPS.Rank` <-
    100 - round(percent_rank(x$`Price/CFPS`) * 100, 1)
  x$`Shareholder Yield.Rank` <-
    round(percent_rank(x$`Shareholder Yield`) * 100, 1)
  
  #Stocks with no rank get 50
  x$`Price/Book.Rank`[is.na(x$`Price/Book.Rank`)] <- 50
  x$PE.Rank[is.na(x$PE.Rank)] <- 50
  x$`Price/Sales.Rank`[is.na(x$`Price/Sales.Rank`)] <- 50
  x$`Enterprise Value/EBITDA.Rank`[is.na(x$`Enterprise Value/EBITDA.Rank`)] <-
    50
  x$`Price/CFPS.Rank`[is.na(x$`Price/CFPS.Rank`)] <- 50
  x$`Shareholder Yield.Rank`[is.na(x$`Shareholder Yield.Rank`)] <- 50
  #Sum the Ranks
  x$SumRank <-
    x$`Price/Book.Rank` + x$PE.Rank + x$`Price/Sales.Rank` + x$`Enterprise Value/EBITDA.Rank` + x$`Price/CFPS.Rank` + x$`Shareholder Yield.Rank`
  x$VC2 <- round(percent_rank(x$SumRank) * 100, 1)
  return(x)
}

allstocks <- calcvc2(allstocks)
largestocks <- calcvc2(largestocks)
marketleaders <- calcvc2(marketleaders)

# Portfolios

## Trending Value

In [9]:
TrendingValue <- allstocks %>%  filter(VC2 >= 90) %>% arrange(desc(`Price Change 26 week`)) %>% slice_head(n = 25) %>% select(Ticker, `Company name`,Sector,Industry)

TrendingValue %>%
  kable("html") %>%
  as.character() %>%
  display_html()

Ticker 
 Company name 
 Sector 
 Industry 
 
 
 
 
 TGA 
 TransGlobe Energy Corporation 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 TGL 
 TransGlobe Energy Corporation 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 GRIN 
 Grindrod Shipping Holdings Ltd 
 52 - Industrials 
 52405020 - Freight & Logistics - Marine 
 
 
 VHI 
 Valhi, Inc. 
 51 - Basic Materials 
 51101030 - Chemicals - Specialty 
 
 
 PANL 
 Pangaea Logistics Solutions Lt 
 52 - Industrials 
 52405020 - Freight & Logistics - Marine 
 
 
 APA 
 APA Corp (US) 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 UONEK 
 Urban One Inc 
 53 - Consumer Cyclicals 
 53302020 - Broadcasting 
 
 
 GNK 
 Genco Shipping & Trading Limit 
 52 - Industrials 
 52405020 - Freight & Logistics - Marine 
 
 
 LPG 
 Dorian LPG Ltd 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 GOGL 
 Golden Ocean Group Ltd 
 52 - Industrials 
 52405020 - Freight & Logistics - Marine 
 
 
 TECK 
 Teck Resources Ltd (USA) 
 51 - Basic Materials 
 51201080 - Metals & Mining - Diversified 
 
 
 TECK.B 
 Teck Resources Ltd 
 51 - Basic Materials 
 51201080 - Metals & Mining - Diversified 
 
 
 TMST 
 Timkensteel Corp 
 51 - Basic Materials 
 51201020 - Metals & Mining - Iron & Steel 
 
 
 HCC 
 Warrior Met Coal Inc 
 51 - Basic Materials 
 51201020 - Metals & Mining - Iron & Steel 
 
 
 ZEUS 
 Olympic Steel, Inc. 
 51 - Basic Materials 
 51201020 - Metals & Mining - Iron & Steel 
 
 
 IMO 
 Imperial Oil Ltd 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 DSX 
 Diana Shipping Inc 
 52 - Industrials 
 52405020 - Freight & Logistics - Marine 
 
 
 UAN 
 CVR Partners LP 
 51 - Basic Materials 
 51101020 - Chemicals - Agricultural 
 
 
 UNM 
 Unum Group 
 55 - Financials 
 55301030 - Insurance - Life & Health 
 
 
 SBLK 
 Star Bulk Carriers Corp. 
 52 - Industrials 
 52405020 - Freight & Logistics - Marine 
 
 
 NRP 
 Natural Resource Partners LP 
 50 - Energy 
 50101010 - Coal 
 
 
 UFCS 
 United Fire Group, Inc. 
 55 - Financials 
 55301020 - Insurance - Property & Casualty 
 
 
 STLD 
 Steel Dynamics, Inc. 
 51 - Basic Materials 
 51201020 - Metals & Mining - Iron & Steel 
 
 
 NTR 
 Nutrien Ltd 
 51 - Basic Materials 
 51101020 - Chemicals - Agricultural 
 
 
 AGRO 
 Adecoagro SA 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing

## Cheap Stocks on the mend

In [10]:
cheapmend <-
  allstocks %>%  filter(VC2 >= 70) %>% filter(`Price Change 13 week` > median13w) %>% filter(`Price Change 26 week` >
                                        median26w) %>% arrange(desc(`Price Change 26 week`)) %>%             
                                        slice_head(n = 25) %>% select(Ticker, `Company name`)

cheapmend %>%
  kable("html") %>%
  as.character() %>%
  display_html()

Ticker 
 Company name 
 
 
 
 
 AMR 
 Alpha Metallurgical Resources 
 
 
 OBE 
 Obsidian Energy Ltd 
 
 
 PBF 
 PBF Energy Inc 
 
 
 AMPY 
 Amplify Energy Corp 
 
 
 BTU 
 Peabody Energy Corporation 
 
 
 CEIX 
 Consol Energy Inc 
 
 
 CVI 
 CVR Energy, Inc. 
 
 
 WTI 
 W&T Offshore, Inc. 
 
 
 HMLP 
 Hoegh LNG Partners LP 
 
 
 VET 
 Vermilion Energy Inc 
 
 
 BTE 
 Baytex Energy Corp 
 
 
 CPG 
 Crescent Point Energy Corp 
 
 
 ARLP 
 Alliance Resource Partners, L. 
 
 
 TRQ 
 Turquoise Hill Resources Ltd 
 
 
 MRO 
 Marathon Oil Corporation 
 
 
 CVE 
 Cenovus Energy Inc (US) 
 
 
 ARCH 
 Arch Resources Inc 
 
 
 TGA 
 TransGlobe Energy Corporation 
 
 
 TGL 
 TransGlobe Energy Corporation 
 
 
 GRIN 
 Grindrod Shipping Holdings Ltd 
 
 
 VHI 
 Valhi, Inc. 
 
 
 EGLE 
 Eagle Bulk Shipping Inc. 
 
 
 PANL 
 Pangaea Logistics Solutions Lt 
 
 
 APA 
 APA Corp (US) 
 
 
 UONEK 
 Urban One Inc

## Market Leaders

### Price Appreciation

In [11]:
mlsy <- marketleaders %>% filter(`Price Change 13 week` > median13w) %>% 
  filter(`Price Change 26 week` >median26w) %>% 
  arrange(desc(`Shareholder Yield`)) %>%
  slice_head(n = 25) %>% 
  select(Ticker, `Company name`,Sector,Industry)
mlsy %>%
  kable("html") %>%
  as.character() %>%
  display_html()

Ticker 
 Company name 
 Sector 
 Industry 
 
 
 
 
 MPC 
 Marathon Petroleum Corp 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 LUMN 
 Lumen Technologies Inc 
 57 - Technology 
 57401010 - Telecommunications Services - Integrated 
 
 
 IMO 
 Imperial Oil Ltd 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 MPLX 
 MPLX LP 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 ALL 
 Allstate Corp 
 55 - Financials 
 55301020 - Insurance - Property & Casualty 
 
 
 MET 
 Metlife Inc 
 55 - Financials 
 55301030 - Insurance - Life & Health 
 
 
 PAA 
 Plains All American Pipeline, 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 PRU 
 Prudential Financial Inc 
 55 - Financials 
 55301030 - Insurance - Life & Health 
 
 
 SU 
 Suncor Energy Inc. (USA) 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 HIG 
 Hartford Financial Services Gr 
 55 - Financials 
 55301010 - Insurance - Multiline & Brokers 
 
 
 MO 
 Altria Group Inc 
 54 - Consumer Non-Cyclicals 
 54102030 - Tobacco 
 
 
 PFG 
 Principal Financial Group Inc 
 55 - Financials 
 55301030 - Insurance - Life & Health 
 
 
 AMGN 
 Amgen, Inc. 
 56 - Healthcare 
 56201040 - Pharmaceuticals 
 
 
 DVN 
 Devon Energy Corp 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 L 
 Loews Corporation 
 55 - Financials 
 55301020 - Insurance - Property & Casualty 
 
 
 CB 
 Chubb Ltd 
 55 - Financials 
 55301010 - Insurance - Multiline & Brokers 
 
 
 FLEX 
 Flex Ltd 
 57 - Technology 
 57104010 - Electronic Equipment & Parts 
 
 
 UBS 
 UBS Group AG (USA) 
 55 - Financials 
 55102020 - Investment Management & Fund Operators 
 
 
 PAGP 
 Plains GP Holdings LP 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 BMY 
 Bristol-Myers Squibb Co 
 56 - Healthcare 
 56201040 - Pharmaceuticals 
 
 
 EPD 
 Enterprise Products Partners L 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 ACGL 
 Arch Capital Group Ltd. 
 55 - Financials 
 55301020 - Insurance - Property & Casualty 
 
 
 TRV 
 Travelers Companies Inc 
 55 - Financials 
 55301020 - Insurance - Property & Casualty 
 
 
 AMCR 
 Amcor PLC 
 51 - Basic Materials 
 51302010 - Non-Paper Containers & Packaging 
 
 
 LYB 
 LyondellBasell Industries NV 
 51 - Basic Materials 
 51101010 - Chemicals - Commodity

In [12]:
mlvc2 <- marketleaders %>% filter(`Price Change 13 week` > median13w) %>% 
  filter(`Price Change 26 week` >median26w) %>% 
  arrange(desc(VC2)) %>%
  slice_head(n = 25) %>% 
  select(Ticker, `Company name`,Sector,Industry)
mlvc2 %>%
  kable("html") %>%
  as.character() %>%
  display_html()

Ticker 
 Company name 
 Sector 
 Industry 
 
 
 
 
 MET 
 Metlife Inc 
 55 - Financials 
 55301030 - Insurance - Life & Health 
 
 
 LUMN 
 Lumen Technologies Inc 
 57 - Technology 
 57401010 - Telecommunications Services - Integrated 
 
 
 T 
 AT&T Inc. 
 57 - Technology 
 57401020 - Telecommunications Services - Wireless 
 
 
 FLEX 
 Flex Ltd 
 57 - Technology 
 57104010 - Electronic Equipment & Parts 
 
 
 MFC 
 Manulife Financial Corporation 
 55 - Financials 
 55301030 - Insurance - Life & Health 
 
 
 IMO 
 Imperial Oil Ltd 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 UBS 
 UBS Group AG (USA) 
 55 - Financials 
 55102020 - Investment Management & Fund Operators 
 
 
 HIG 
 Hartford Financial Services Gr 
 55 - Financials 
 55301010 - Insurance - Multiline & Brokers 
 
 
 PRU 
 Prudential Financial Inc 
 55 - Financials 
 55301030 - Insurance - Life & Health 
 
 
 TECK.B 
 Teck Resources Ltd 
 51 - Basic Materials 
 51201080 - Metals & Mining - Diversified 
 
 
 ALL 
 Allstate Corp 
 55 - Financials 
 55301020 - Insurance - Property & Casualty 
 
 
 L 
 Loews Corporation 
 55 - Financials 
 55301020 - Insurance - Property & Casualty 
 
 
 HUN 
 Huntsman Corporation 
 51 - Basic Materials 
 51101090 - Chemicals - Diversified 
 
 
 LYB 
 LyondellBasell Industries NV 
 51 - Basic Materials 
 51101010 - Chemicals - Commodity 
 
 
 MPC 
 Marathon Petroleum Corp 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 PFG 
 Principal Financial Group Inc 
 55 - Financials 
 55301030 - Insurance - Life & Health 
 
 
 TSN 
 Tyson Foods, Inc. 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 ACGL 
 Arch Capital Group Ltd. 
 55 - Financials 
 55301020 - Insurance - Property & Casualty 
 
 
 TECK 
 Teck Resources Ltd (USA) 
 51 - Basic Materials 
 51201080 - Metals & Mining - Diversified 
 
 
 DELL 
 Dell Technologies Inc 
 57 - Technology 
 57106010 - Computer Hardware 
 
 
 TRV 
 Travelers Companies Inc 
 55 - Financials 
 55301020 - Insurance - Property & Casualty 
 
 
 SU 
 Suncor Energy Inc. (USA) 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 MOS 
 Mosaic Co 
 51 - Basic Materials 
 51101020 - Chemicals - Agricultural 
 
 
 TEVA 
 Teva Pharmaceutical Industries 
 56 - Healthcare 
 56201040 - Pharmaceuticals 
 
 
 DB 
 Deutsche Bank AG (USA) 
 55 - Financials 
 55101010 - Banks

In [13]:
unique(arrange(rbind(mlvc2,mlsy),Ticker)) %>%
  kable("html") %>%
  as.character() %>%
  display_html()

Ticker 
 Company name 
 Sector 
 Industry 
 
 
 
 
 1 
 ACGL 
 Arch Capital Group Ltd. 
 55 - Financials 
 55301020 - Insurance - Property & Casualty 
 
 
 3 
 ALL 
 Allstate Corp 
 55 - Financials 
 55301020 - Insurance - Property & Casualty 
 
 
 5 
 AMCR 
 Amcor PLC 
 51 - Basic Materials 
 51302010 - Non-Paper Containers & Packaging 
 
 
 6 
 AMGN 
 Amgen, Inc. 
 56 - Healthcare 
 56201040 - Pharmaceuticals 
 
 
 7 
 BMY 
 Bristol-Myers Squibb Co 
 56 - Healthcare 
 56201040 - Pharmaceuticals 
 
 
 8 
 CB 
 Chubb Ltd 
 55 - Financials 
 55301010 - Insurance - Multiline & Brokers 
 
 
 9 
 DB 
 Deutsche Bank AG (USA) 
 55 - Financials 
 55101010 - Banks 
 
 
 10 
 DELL 
 Dell Technologies Inc 
 57 - Technology 
 57106010 - Computer Hardware 
 
 
 11 
 DVN 
 Devon Energy Corp 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 12 
 EPD 
 Enterprise Products Partners L 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 13 
 FLEX 
 Flex Ltd 
 57 - Technology 
 57104010 - Electronic Equipment & Parts 
 
 
 15 
 HIG 
 Hartford Financial Services Gr 
 55 - Financials 
 55301010 - Insurance - Multiline & Brokers 
 
 
 17 
 HUN 
 Huntsman Corporation 
 51 - Basic Materials 
 51101090 - Chemicals - Diversified 
 
 
 18 
 IMO 
 Imperial Oil Ltd 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 20 
 L 
 Loews Corporation 
 55 - Financials 
 55301020 - Insurance - Property & Casualty 
 
 
 22 
 LUMN 
 Lumen Technologies Inc 
 57 - Technology 
 57401010 - Telecommunications Services - Integrated 
 
 
 24 
 LYB 
 LyondellBasell Industries NV 
 51 - Basic Materials 
 51101010 - Chemicals - Commodity 
 
 
 26 
 MET 
 Metlife Inc 
 55 - Financials 
 55301030 - Insurance - Life & Health 
 
 
 28 
 MFC 
 Manulife Financial Corporation 
 55 - Financials 
 55301030 - Insurance - Life & Health 
 
 
 29 
 MO 
 Altria Group Inc 
 54 - Consumer Non-Cyclicals 
 54102030 - Tobacco 
 
 
 30 
 MOS 
 Mosaic Co 
 51 - Basic Materials 
 51101020 - Chemicals - Agricultural 
 
 
 31 
 MPC 
 Marathon Petroleum Corp 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 33 
 MPLX 
 MPLX LP 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 34 
 PAA 
 Plains All American Pipeline, 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 35 
 PAGP 
 Plains GP Holdings LP 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 36 
 PFG 
 Principal Financial Group Inc 
 55 - Financials 
 55301030 - Insurance - Life & Health 
 
 
 38 
 PRU 
 Prudential Financial Inc 
 55 - Financials 
 55301030 - Insurance - Life & Health 
 
 
 40 
 SU 
 Suncor Energy Inc. (USA) 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 42 
 T 
 AT&T Inc. 
 57 - Technology 
 57401020 - Telecommunications Services - Wireless 
 
 
 43 
 TECK 
 Teck Resources Ltd (USA) 
 51 - Basic Materials 
 51201080 - Metals & Mining - Diversified 
 
 
 44 
 TECK.B 
 Teck Resources Ltd 
 51 - Basic Materials 
 51201080 - Metals & Mining - Diversified 
 
 
 45 
 TEVA 
 Teva Pharmaceutical Industries 
 56 - Healthcare 
 56201040 - Pharmaceuticals 
 
 
 46 
 TRV 
 Travelers Companies Inc 
 55 - Financials 
 55301020 - Insurance - Property & Casualty 
 
 
 48 
 TSN 
 Tyson Foods, Inc. 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 49 
 UBS 
 UBS Group AG (USA) 
 55 - Financials 
 55102020 - Investment Management & Fund Operators

In [14]:
utilities <- allstocks %>%
  filter(Sector == "59  - Utilities") %>%
  arrange(desc(VC2)) %>%
  slice_head(n =25) %>% 
  select(Ticker, `Company name`,Sector,Industry)
  
noncyc <- filter(allstocks,Sector == "54  - Consumer Non-Cyclicals") %>%
  arrange(desc(`Shareholder Yield`)) %>%
  slice_head(n = 25) %>% 
  select(Ticker, `Company name`,Sector,Industry)
  
arrange(rbind(utilities,noncyc),Ticker)   %>%
  kable("html") %>%
  as.character() %>%
  display_html()

constap <- rbind(slice_head(noncyc,n=3),slice_head(utilities,n=3))

Ticker 
 Company name 
 Sector 
 Industry 
 
 
 
 
 AGRO 
 Adecoagro SA 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 ALE 
 ALLETE Inc 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 AVA 
 Avista Corp 
 59 - Utilities 
 59104010 - Utilities - Multiline 
 
 
 AY 
 Atlantica Sustainable Infrastr 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 BKH 
 Black Hills Corp 
 59 - Utilities 
 59104010 - Utilities - Multiline 
 
 
 CAG 
 Conagra Brands Inc 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 CAH 
 Cardinal Health Inc 
 54 - Consumer Non-Cyclicals 
 54301010 - Retailers - Drug 
 
 
 CLX 
 Clorox Co 
 54 - Consumer Non-Cyclicals 
 54201010 - Household Products 
 
 
 COKE 
 Coca-Cola Consolidated Inc 
 54 - Consumer Non-Cyclicals 
 54101030 - Non-Alcoholic Beverages 
 
 
 CSV 
 Carriage Services, Inc. 
 54 - Consumer Non-Cyclicals 
 54201030 - Personal Services 
 
 
 EIX 
 Edison International 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 ETR 
 Entergy Corporation 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 EVRG 
 Evergy Inc 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 EXC 
 Exelon Corporation 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 HAIN 
 Hain Celestial Group Inc 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 HE 
 Hawaiian Electric Industries, 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 HLF 
 Herbalife Nutrition Ltd 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 HRB 
 H & R Block Inc 
 54 - Consumer Non-Cyclicals 
 54201030 - Personal Services 
 
 
 KEN 
 Kenon Holdings Ltd 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 KR 
 Kroger Co 
 54 - Consumer Non-Cyclicals 
 54301020 - Food Retail & Distribution 
 
 
 MCK 
 McKesson Corporation 
 54 - Consumer Non-Cyclicals 
 54301010 - Retailers - Drug 
 
 
 MDU 
 Mdu Resources Group Inc 
 59 - Utilities 
 59104010 - Utilities - Multiline 
 
 
 MED 
 Medifast Inc 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 MIC 
 Macquarie Infrastructure Holdi 
 59 - Utilities 
 59102010 - Utilities - Natural Gas 
 
 
 MMM 
 3M Co 
 54 - Consumer Non-Cyclicals 
 54401010 - Consumer Goods Conglomerates 
 
 
 MO 
 Altria Group Inc 
 54 - Consumer Non-Cyclicals 
 54102030 - Tobacco 
 
 
 NRG 
 NRG Energy Inc 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 OGE 
 OGE Energy Corp. 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 OTTR 
 Otter Tail Corporation 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 PCG 
 PG&E Corporation 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 PETS 
 Petmed Express Inc 
 54 - Consumer Non-Cyclicals 
 54301010 - Retailers - Drug 
 
 
 PM 
 Philip Morris International In 
 54 - Consumer Non-Cyclicals 
 54102030 - Tobacco 
 
 
 PNM 
 PNM Resources Inc 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 PNW 
 Pinnacle West Capital Corporat 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 POR 
 Portland General Electric Comp 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 PPL 
 PPL Corp 
 59 - Utilities 
 59104010 - Utilities - Multiline 
 
 
 PRG 
 PROG Holdings Inc 
 54 - Consumer Non-Cyclicals 
 54201030 - Personal Services 
 
 
 SCI 
 Service Corporation Internatio 
 54 - Consumer Non-Cyclicals 
 54201030 - Personal Services 
 
 
 SENEA 
 Seneca Foods Corp 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 SFM 
 Sprouts Farmers Market Inc 
 54 - Consumer Non-Cyclicals 
 54301020 - Food Retail & Distribution 
 
 
 SJM 
 J M Smucker Co 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 SR 
 Spire Inc 
 59 - Utilities 
 59102010 - Utilities - Natural Gas 
 
 
 TAC 
 TransAlta Corporation (USA) 
 59 - Utilities 
 59101020 - Utilities - Independent Power Producers 
 
 
 TPB 
 Turning Point Brands Inc 
 54 - Consumer Non-Cyclicals 
 54102030 - Tobacco 
 
 
 UGI 
 UGI Corp 
 59 - Utilities 
 59102010 - Utilities - Natur

## My 24 stock port

In [15]:
n <-1
c <-1
while(c < 12)  {
  mlC <- unique(rbind(slice_head(mlvc2,n=n),slice_head(mlsy,n=n)))
  n <- n + 1
  c = nrow(mlC)
}

n <-1
c <-1
rportTemp <- rbind(slice_head(mlC, n=6),constap)
while(c < 25)  {

rport <- unique(rbind(rportTemp,slice_head(TrendingValue,n=n)))
  n <- n + 1
  c = nrow(rport)
}
rport %>%
  kable("html") %>%
  as.character() %>%
  display_html()

Ticker 
 Company name 
 Sector 
 Industry 
 
 
 
 
 MET 
 Metlife Inc 
 55 - Financials 
 55301030 - Insurance - Life & Health 
 
 
 LUMN 
 Lumen Technologies Inc 
 57 - Technology 
 57401010 - Telecommunications Services - Integrated 
 
 
 T 
 AT&T Inc. 
 57 - Technology 
 57401020 - Telecommunications Services - Wireless 
 
 
 FLEX 
 Flex Ltd 
 57 - Technology 
 57104010 - Electronic Equipment & Parts 
 
 
 MFC 
 Manulife Financial Corporation 
 55 - Financials 
 55301030 - Insurance - Life & Health 
 
 
 IMO 
 Imperial Oil Ltd 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 VLGEA 
 Village Super Market, Inc. 
 54 - Consumer Non-Cyclicals 
 54301020 - Food Retail & Distribution 
 
 
 COKE 
 Coca-Cola Consolidated Inc 
 54 - Consumer Non-Cyclicals 
 54101030 - Non-Alcoholic Beverages 
 
 
 PRG 
 PROG Holdings Inc 
 54 - Consumer Non-Cyclicals 
 54201030 - Personal Services 
 
 
 NRG 
 NRG Energy Inc 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 VIA 
 Via Renewables Inc 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 UGI 
 UGI Corp 
 59 - Utilities 
 59102010 - Utilities - Natural Gas 
 
 
 TGA 
 TransGlobe Energy Corporation 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 TGL 
 TransGlobe Energy Corporation 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 GRIN 
 Grindrod Shipping Holdings Ltd 
 52 - Industrials 
 52405020 - Freight & Logistics - Marine 
 
 
 VHI 
 Valhi, Inc. 
 51 - Basic Materials 
 51101030 - Chemicals - Specialty 
 
 
 PANL 
 Pangaea Logistics Solutions Lt 
 52 - Industrials 
 52405020 - Freight & Logistics - Marine 
 
 
 APA 
 APA Corp (US) 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 UONEK 
 Urban One Inc 
 53 - Consumer Cyclicals 
 53302020 - Broadcasting 
 
 
 GNK 
 Genco Shipping & Trading Limit 
 52 - Industrials 
 52405020 - Freight & Logistics - Marine 
 
 
 LPG 
 Dorian LPG Ltd 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 GOGL 
 Golden Ocean Group Ltd 
 52 - Industrials 
 52405020 - Freight & Logistics - Marine 
 
 
 TECK 
 Teck Resources Ltd (USA) 
 51 - Basic Materials 
 51201080 - Metals & Mining - Diversified 
 
 
 TECK.B 
 Teck Resources Ltd 
 51 - Basic Materials 
 51201080 - Metals & Mining - Diversified 
 
 
 TMST 
 Timkensteel Corp 
 51 - Basic Materials 
 51201020 - Metals & Mining - Iron & Steel